# EXAMEN DE SIMULACIÓN - PRIMER INTERCICLO
### Alejandro Enríquez 
### Ingeniería en Ciencias de la Computación
### 9no Ciclo

## - PARTE 1 - REGRESIÓN 

In [1]:
# Imports

import pandas as pd
import numpy as np
from datetime import datetime
from matplotlib import pyplot as plt
import matplotlib.patches as mpatches
from datetime import datetime,timedelta
from sklearn.model_selection import train_test_split as tts
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_absolute_error
from datetime import datetime
from datetime import timedelta

In [2]:
# Carga y procesamiento de datos
data = pd.read_csv('Lasso.csv')

# Creación del dataframe para el procesamiento
data_lasso = pd.DataFrame(columns=['texto','comentarios','compartidos'])
data_lasso['texto'] = data['Text2']
data_lasso['comentarios'] = data['Text3']
data_lasso['compartidos'] = data['Text4']

# Procesamiento de textos
#Quitar los saltos de linea, espacios y caracteres raros
for i, ix in enumerate(data_lasso['texto']):
    data_lasso['texto'][i] = str(data_lasso['texto'][i]).replace(' \n', '. ').replace('\n', '').replace('🇪🇨','')
    data_lasso['texto'][i] = str(data_lasso['texto'][i]).lower()

# Quitar los espacios y caracteres no deseados para posteriormente transformar a número
for i in range(len(data_lasso['comentarios'])):
    data_lasso['comentarios'][i] = str(data_lasso['comentarios'][i]).replace(' ', '')
    if ',' in str(data_lasso['comentarios'][i]):
        data_lasso['comentarios'][i] = str(data_lasso['comentarios'][i]).replace(',','').replace('mil','')+"00"
    elif 'mil' in str(data_lasso['comentarios'][i]):
        data_lasso['comentarios'][i] = str(data_lasso['comentarios'][i]).replace('mil', '').replace('comentarios', '')+'000'
    else:
        data_lasso['comentarios'][i] = str(data_lasso['comentarios'][i]).replace('comentarios', '')
        
# Quitar los espacios y caracteres no deseados para posteriormente transformar a número
for i in range(len(data_lasso['compartidos'])):
    data_lasso['compartidos'][i] = str(data_lasso['compartidos'][i]).replace(' ', '')
    if ',' in str(data_lasso['compartidos'][i]):
        data_lasso['compartidos'][i] = str(data_lasso['compartidos'][i]).replace(',','').replace('mil','').replace('vecescompartido', '')+"00"
    elif 'mil' in str(data_lasso['compartidos'][i]):
        data_lasso['compartidos'][i] = str(data_lasso['compartidos'][i]).replace('mil', '').replace('vecescompartido', '')+'000'
    else:
        data_lasso['compartidos'][i] = str(data_lasso['compartidos'][i]).replace('vecescompartido', '')
       
# Quitar valores NaN y poner 0
data_lasso['comentarios'] = data_lasso['comentarios'].fillna(0)
data_lasso['compartidos'] = data_lasso['compartidos'].fillna(0)

# Reemplazar textos nan por 0
for i in range(len(data_lasso['comentarios'])):
    data_lasso['comentarios'][i] = str(data_lasso['comentarios'][i]).replace('nan','0')
    data_lasso['compartidos'][i] = str(data_lasso['compartidos'][i]).replace('nan','0')

# Convertir textos a números
data_lasso['comentarios'] = data_lasso['comentarios'].apply(pd.to_numeric)
data_lasso['compartidos'] = data_lasso['compartidos'].apply(pd.to_numeric)

# Ordenar
data_lasso = data_lasso.sort_values(by=['comentarios']).reset_index(drop=True)  


IndentationError: unexpected indent (<ipython-input-2-602fb61061db>, line 2)

In [ ]:
palabras = ['covid', 'cuador', 'ecuatorianos', 'restricciones', 'lasso','de', 'la', 'los']
concurrencias = []
for i in range(len(data_lasso['texto'])):
    cont = 0
    d = data_lasso['texto'][i]
    for j in range(len(palabras)):
        if palabras[j] in d:
            cont+=1
    concurrencias.append(cont)

data_lasso['concurrencias'] = concurrencias

In [ ]:
# Entrenamiento 
xtrain, xtest, ytrain, ytest = tts(data_lasso['concurrencias'], data_lasso['comentarios'], test_size=0.2)
modelo = LinearRegression()
entrenamiento = np.array(xtrain).reshape(-1,1)
prueba = np.array(xtest).reshape(-1,1)
modelo.fit(entrenamiento, ytrain)

pred = modelo.predict(prueba)
xtest = xtest.sort_values()

In [ ]:
# Calcular Error 
mae = mean_absolute_error(ytest, pred)
mae

In [ ]:
# Gráfico
resultados = pd.DataFrame(data=[xtest.reset_index(drop=True), ytest.reset_index(drop=True), pred], columns=np.arange(len(xtest)), index=['concurrencias', 'comentarios', 'prediccion']).T
resultados = resultados.groupby('concurrencias').sum()

plt.bar(resultados.index - 0.2, resultados['comentarios'], width = 0.4, label = 'REAL')
plt.bar(resultados.index + 0.2, resultados['prediccion'], width = 0.4, label = 'PREDICCIÓN')
plt.legend()

# PARTE 2 - SIMULACIÓN EN SIMPY


In [3]:
# Imports
import simpy
import random
import pandas as pd
import numpy as np
from matplotlib import pyplot as plt

In [4]:
# Instanciar Variables
horas_diarias = 9
minutos_diarios = horas_diarias * 60

TIEMPO_TOTAL = minutos_diarios * 100
NUM_MEDICOS = 6
TIEMPO_VACUNACION = 5 #Hasta 10
INTERVALO_LLEGADA = 5
POST_VACUNA = 20
CERTIFICACION = 2 #Hasta 3
TOTAL_DIAS = 100
ESPERA_INICIAL = 6

vacunados = 0
no_vacunados = 0
pacientes = 0
bandera = 1

proceso = pd.DataFrame(columns=['dia','pacientes','vacunados','no_vacunados'])

In [5]:
# Clase 
class Vacunacion(object):
    def __init__(self, environment, num_medicos, tiempo_vacunacion):
        self.env = environment
        self.medicos = simpy.Resource(environment, num_medicos)
        
    def vacunar(self, paciente):
        complicaciones = random.randint(1,100)
        global vacunados
        global no_vacunados
        global bandera
        if(complicaciones<95):
            tVacunacion = random.randint(TIEMPO_VACUNACION, TIEMPO_VACUNACION+5)
            print("El paciente %s empieza la vacunación a la hora: %.2f." %(paciente, env.now))
            yield self.env.timeout(tVacunacion)
            vacunados+=1
            bandera = 1
        else:
            print("*** El %s No puede vacunarse" % (paciente))
            no_vacunados+=1
            bandera = 0
            
    def revisar(self, paciente):
        global bandera
        print('Empieza espera: %s a la hora %.2f.' % (paciente, env.now))
        tCertificacion = random.randint(CERTIFICACION, CERTIFICACION+1)
        if bandera == 1:
            yield env.timeout(tCertificacion + POST_VACUNA)
            print("[%s]  se retira vacunado y certificado a las %.2f." % (paciente, env.now))
        else:
            print("[%s]  se retira sin ser vacunado a las %.2f." % (paciente, env.now))

In [6]:
# Procesos
def llegada_paciente(env, nombre, vacunacion):
    print("Llega paciente: %s a la hora %.2f." % (nombre, env.now))
    with vacunacion.medicos.request() as medico:
        yield medico
        #print('Empieza vacunación: %s a la hora %.2f.' % (nombre, env.now))
        yield env.process(vacunacion.vacunar(nombre))
        print('La vacunacion de %s terminó a la hora: %.2f.'%(nombre, env.now))
        env.process(vacunacion.revisar(nombre))
        print("[%s]  se retira a las %.2f." % (nombre, env.now))
        
def ejecutar_simulacion(env, num_medicos, tiempo_vacunacion, intervalo):
    global pacientes
    global ESPERA_INICIAL
    vacunacion = Vacunacion(env, num_medicos, tiempo_vacunacion)
    for i in range(ESPERA_INICIAL):
        env.process(llegada_paciente(env, 'Paciente-%d' % (i+1), vacunacion))
        
    while True:
        yield env.timeout(random.randint(intervalo-3, intervalo+2))
        i+=1   
        env.process(llegada_paciente(env, 'Paciente-%d' % (i+1), vacunacion))
        pacientes = i+1

In [7]:
# Simulación
print("Iniciando vacunacion")
random.seed(76)

for i in range(TOTAL_DIAS):
    env = simpy.Environment()
    print("###Los médicos del día ", i, " son: ", NUM_MEDICOS)
    env.process(ejecutar_simulacion(env, NUM_MEDICOS, TIEMPO_VACUNACION, INTERVALO_LLEGADA))
    env.run(until=minutos_diarios)
    dia = [i+1, pacientes, vacunados, no_vacunados]
    proceso.loc[len(proceso)] = dia
    vacunados = 0
    no_vacunados = 0
    if i >= 30:
        NUM_MEDICOS = 10
        INTERVALO_LLEGADA = 4
    else:
        NUM_MEDICOS = 6
        INTERVALO_LLEGADA = 5
            

Iniciando vacunacion
###Los médicos del día  0  son:  6
Llega paciente: Paciente-1 a la hora 0.00.
Llega paciente: Paciente-2 a la hora 0.00.
Llega paciente: Paciente-3 a la hora 0.00.
Llega paciente: Paciente-4 a la hora 0.00.
Llega paciente: Paciente-5 a la hora 0.00.
Llega paciente: Paciente-6 a la hora 0.00.
El paciente Paciente-1 empieza la vacunación a la hora: 0.00.
El paciente Paciente-2 empieza la vacunación a la hora: 0.00.
El paciente Paciente-3 empieza la vacunación a la hora: 0.00.
El paciente Paciente-4 empieza la vacunación a la hora: 0.00.
El paciente Paciente-5 empieza la vacunación a la hora: 0.00.
El paciente Paciente-6 empieza la vacunación a la hora: 0.00.
Llega paciente: Paciente-7 a la hora 4.00.
Llega paciente: Paciente-8 a la hora 6.00.
La vacunacion de Paciente-6 terminó a la hora: 6.00.
[Paciente-6]  se retira a las 6.00.
Empieza espera: Paciente-6 a la hora 6.00.
El paciente Paciente-7 empieza la vacunación a la hora: 6.00.
La vacunacion de Paciente-2 termin

[Paciente-12]  se retira vacunado y certificado a las 59.00.
La vacunacion de Paciente-17 terminó a la hora: 59.00.
[Paciente-17]  se retira a las 59.00.
Empieza espera: Paciente-17 a la hora 59.00.
Llega paciente: Paciente-19 a la hora 62.00.
El paciente Paciente-19 empieza la vacunación a la hora: 62.00.
[Paciente-13]  se retira vacunado y certificado a las 63.00.
La vacunacion de Paciente-18 terminó a la hora: 64.00.
[Paciente-18]  se retira a las 64.00.
Empieza espera: Paciente-18 a la hora 64.00.
Llega paciente: Paciente-20 a la hora 67.00.
El paciente Paciente-20 empieza la vacunación a la hora: 67.00.
La vacunacion de Paciente-19 terminó a la hora: 67.00.
[Paciente-19]  se retira a las 67.00.
Empieza espera: Paciente-19 a la hora 67.00.
[Paciente-14]  se retira vacunado y certificado a las 69.00.
[Paciente-15]  se retira vacunado y certificado a las 72.00.
Llega paciente: Paciente-21 a la hora 72.00.
El paciente Paciente-21 empieza la vacunación a la hora: 72.00.
[Paciente-16]  

Empieza espera: Paciente-46 a la hora 184.00.
[Paciente-42]  se retira vacunado y certificado a las 185.00.
Llega paciente: Paciente-49 a la hora 185.00.
El paciente Paciente-49 empieza la vacunación a la hora: 185.00.
Llega paciente: Paciente-50 a la hora 189.00.
El paciente Paciente-50 empieza la vacunación a la hora: 189.00.
La vacunacion de Paciente-48 terminó a la hora: 190.00.
[Paciente-48]  se retira a las 190.00.
Empieza espera: Paciente-48 a la hora 190.00.
La vacunacion de Paciente-49 terminó a la hora: 192.00.
[Paciente-49]  se retira a las 192.00.
Empieza espera: Paciente-49 a la hora 192.00.
Llega paciente: Paciente-51 a la hora 193.00.
El paciente Paciente-51 empieza la vacunación a la hora: 193.00.
Llega paciente: Paciente-52 a la hora 195.00.
El paciente Paciente-52 empieza la vacunación a la hora: 195.00.
[Paciente-43]  se retira vacunado y certificado a las 196.00.
La vacunacion de Paciente-50 terminó a la hora: 196.00.
[Paciente-50]  se retira a las 196.00.
Empieza e

Empieza espera: Paciente-105 a la hora 440.00.
[Paciente-105]  se retira sin ser vacunado a las 440.00.
La vacunacion de Paciente-106 terminó a la hora: 440.00.
[Paciente-106]  se retira a las 440.00.
Empieza espera: Paciente-106 a la hora 440.00.
[Paciente-106]  se retira sin ser vacunado a las 440.00.
[Paciente-98]  se retira vacunado y certificado a las 442.00.
[Paciente-99]  se retira vacunado y certificado a las 442.00.
Llega paciente: Paciente-107 a la hora 442.00.
El paciente Paciente-107 empieza la vacunación a la hora: 442.00.
[Paciente-100]  se retira vacunado y certificado a las 446.00.
Llega paciente: Paciente-108 a la hora 448.00.
El paciente Paciente-108 empieza la vacunación a la hora: 448.00.
[Paciente-102]  se retira vacunado y certificado a las 450.00.
Llega paciente: Paciente-109 a la hora 451.00.
El paciente Paciente-109 empieza la vacunación a la hora: 451.00.
[Paciente-101]  se retira vacunado y certificado a las 452.00.
La vacunacion de Paciente-107 terminó a la 

El paciente Paciente-42 empieza la vacunación a la hora: 162.00.
Llega paciente: Paciente-43 a la hora 164.00.
La vacunacion de Paciente-39 terminó a la hora: 164.00.
[Paciente-39]  se retira a las 164.00.
Empieza espera: Paciente-39 a la hora 164.00.
El paciente Paciente-43 empieza la vacunación a la hora: 164.00.
La vacunacion de Paciente-40 terminó a la hora: 165.00.
[Paciente-40]  se retira a las 165.00.
Empieza espera: Paciente-40 a la hora 165.00.
Llega paciente: Paciente-44 a la hora 166.00.
La vacunacion de Paciente-41 terminó a la hora: 166.00.
[Paciente-41]  se retira a las 166.00.
Empieza espera: Paciente-41 a la hora 166.00.
El paciente Paciente-44 empieza la vacunación a la hora: 166.00.
[Paciente-35]  se retira vacunado y certificado a las 167.00.
La vacunacion de Paciente-42 terminó a la hora: 167.00.
[Paciente-42]  se retira a las 167.00.
Empieza espera: Paciente-42 a la hora 167.00.
[Paciente-36]  se retira vacunado y certificado a las 169.00.
La vacunacion de Paciente

...

Empieza espera: Paciente-100 a la hora 319.00.
La vacunacion de Paciente-101 terminó a la hora: 321.00.
[Paciente-101]  se retira a las 321.00.
Empieza espera: Paciente-101 a la hora 321.00.
Llega paciente: Paciente-104 a la hora 323.00.
El paciente Paciente-104 empieza la vacunación a la hora: 323.00.
Llega paciente: Paciente-105 a la hora 324.00.
El paciente Paciente-105 empieza la vacunación a la hora: 324.00.
[Paciente-95]  se retira vacunado y certificado a las 325.00.
Llega paciente: Paciente-106 a la hora 325.00.
El paciente Paciente-106 empieza la vacunación a la hora: 325.00.
[Paciente-96]  se retira vacunado y certificado a las 326.00.
La vacunacion de Paciente-103 terminó a la hora: 326.00.
[Paciente-103]  se retira a las 326.00.
Empieza espera: Paciente-103 a la hora 326.00.
[Paciente-97]  se retira vacunado y certificado a las 327.00.
Llega paciente: Paciente-107 a la hora 329.00.
El paciente Paciente-107 empieza la vacunación a la hora: 329.00.
La vacunacion de Paciente-1

[Paciente-28]  se retira a las 86.00.
Empieza espera: Paciente-28 a la hora 86.00.
Llega paciente: Paciente-31 a la hora 91.00.
El paciente Paciente-31 empieza la vacunación a la hora: 91.00.
[Paciente-23]  se retira vacunado y certificado a las 92.00.
La vacunacion de Paciente-29 terminó a la hora: 93.00.
[Paciente-29]  se retira a las 93.00.
Empieza espera: Paciente-29 a la hora 93.00.
Llega paciente: Paciente-32 a la hora 94.00.
El paciente Paciente-32 empieza la vacunación a la hora: 94.00.
La vacunacion de Paciente-30 terminó a la hora: 95.00.
[Paciente-30]  se retira a las 95.00.
Empieza espera: Paciente-30 a la hora 95.00.
Llega paciente: Paciente-33 a la hora 97.00.
El paciente Paciente-33 empieza la vacunación a la hora: 97.00.
[Paciente-25]  se retira vacunado y certificado a las 98.00.
La vacunacion de Paciente-31 terminó a la hora: 98.00.
[Paciente-31]  se retira a las 98.00.
Empieza espera: Paciente-31 a la hora 98.00.
La vacunacion de Paciente-32 terminó a la hora: 100.00

Empieza espera: Paciente-106 a la hora 365.00.
Llega paciente: Paciente-108 a la hora 366.00.
El paciente Paciente-108 empieza la vacunación a la hora: 366.00.
Llega paciente: Paciente-109 a la hora 367.00.
El paciente Paciente-109 empieza la vacunación a la hora: 367.00.
[Paciente-101]  se retira vacunado y certificado a las 368.00.
[Paciente-100]  se retira vacunado y certificado a las 369.00.
Llega paciente: Paciente-110 a la hora 370.00.
La vacunacion de Paciente-107 terminó a la hora: 370.00.
[Paciente-107]  se retira a las 370.00.
Empieza espera: Paciente-107 a la hora 370.00.
*** El Paciente-110 No puede vacunarse
La vacunacion de Paciente-110 terminó a la hora: 370.00.
[Paciente-110]  se retira a las 370.00.
Empieza espera: Paciente-110 a la hora 370.00.
[Paciente-110]  se retira sin ser vacunado a las 370.00.
Llega paciente: Paciente-111 a la hora 371.00.
El paciente Paciente-111 empieza la vacunación a la hora: 371.00.
Llega paciente: Paciente-112 a la hora 372.00.
La vacunac

Empieza espera: Paciente-168 a la hora 538.00.
El paciente Paciente-172 empieza la vacunación a la hora: 538.00.
Llega paciente: Paciente-173 a la hora 539.00.
La vacunacion de Paciente-169 terminó a la hora: 539.00.
[Paciente-169]  se retira a las 539.00.
Empieza espera: Paciente-169 a la hora 539.00.
El paciente Paciente-173 empieza la vacunación a la hora: 539.00.
###Los médicos del día  98  son:  10
Llega paciente: Paciente-1 a la hora 0.00.
Llega paciente: Paciente-2 a la hora 0.00.
Llega paciente: Paciente-3 a la hora 0.00.
Llega paciente: Paciente-4 a la hora 0.00.
Llega paciente: Paciente-5 a la hora 0.00.
Llega paciente: Paciente-6 a la hora 0.00.
*** El Paciente-1 No puede vacunarse
El paciente Paciente-2 empieza la vacunación a la hora: 0.00.
El paciente Paciente-3 empieza la vacunación a la hora: 0.00.
El paciente Paciente-4 empieza la vacunación a la hora: 0.00.
El paciente Paciente-5 empieza la vacunación a la hora: 0.00.
El paciente Paciente-6 empieza la vacunación a la 

El paciente Paciente-47 empieza la vacunación a la hora: 141.00.
Llega paciente: Paciente-48 a la hora 142.00.
El paciente Paciente-48 empieza la vacunación a la hora: 142.00.
[Paciente-36]  se retira vacunado y certificado a las 143.00.
La vacunacion de Paciente-44 terminó a la hora: 143.00.
[Paciente-44]  se retira a las 143.00.
Empieza espera: Paciente-44 a la hora 143.00.
La vacunacion de Paciente-45 terminó a la hora: 144.00.
[Paciente-45]  se retira a las 144.00.
Empieza espera: Paciente-45 a la hora 144.00.
[Paciente-39]  se retira vacunado y certificado a las 145.00.
La vacunacion de Paciente-46 terminó a la hora: 145.00.
[Paciente-46]  se retira a las 145.00.
Empieza espera: Paciente-46 a la hora 145.00.
[Paciente-38]  se retira vacunado y certificado a las 146.00.
[Paciente-37]  se retira vacunado y certificado a las 147.00.
Llega paciente: Paciente-49 a la hora 147.00.
El paciente Paciente-49 empieza la vacunación a la hora: 147.00.
La vacunacion de Paciente-48 terminó a la 

In [ ]:
# Gráfica y resultados
fig = plt.figure(figsize=(20,10))

ax = fig.add_axes([0,0,1,1])
ax.bar(proceso['dia'], proceso['vacunados'])
plt.title('Proceso de vacunación por días')
plt.show()

ax1 = plt.figure(figsize=(20,10))
total_poblacion = 17700000 * 80 / 100
total_junta = 14211 * 80 / 100
total = sum(proceso['vacunados'])
total_noVacuna = sum(proceso['no_vacunados'])

labels = ['Total Junta', 'Simulación Vacunados', 'Simulación No Vacunados']
datos = [total_junta, total, total_noVacuna]

plt.bar(labels, datos)